# Visualizing Mapillary Data on GCP

This short notebook demostrates how we can access and visualize data was imported from Mapillary and stored on CGP.


### Authenticating with Google Cloud

Before we can run this notebook on a new device, we will have to authenticate with google cloud. To do so, please run the following command in a terminal window (you shouldn't need to do this if you have already authenticated on this device):

```
gcloud auth application-default login 
```

Now we can continue with importing the python modules that we will use.

In [1]:
import folium
import numpy as np

from src.controller import MapillaryImage
from src.visualizer import Visualize

## Setting Environmental Variables

In order for the importer module to access both Google Storage and the Mapillary API, the following environmental variables must be set. Replace the text in `<>` with actual variables before running the next block.

In [2]:
%env DATABASE_URL=<database_url>

env: DATABASE_URL=postgresql://admin:NKbu5:$c7QyA{+-Z@104.198.127.192:5432/mapillary


## Get Data from Database by Bounding Box

In order to visualize the data, we will need to query the database and have the data in a Python data type. The `MapillaryImage` controller class contains functions to return data from the database in various formats. We will use it to construct a Geopandas dataframe of data that falls within some bounding box of interest.

First, initialize the controller:

In [3]:
imgs = MapillaryImage()

Then, set parameters:

In [ ]:
bbox = [141.028,42.292,141.121,42.444]

Now, fetch the data:

In [4]:
data = imgs.select_within_bbox(bbox)

Reading from table. This could take a while ...
done


We can observe the total number of rows of the data and take a look at the first few rows:

In [9]:
print(f"The number of rows returned is: {len(data.index)}")
data.head()

The number of rows returned is: 1608


id                             seq  altitude  \
0  1316223008780318  4EDJVt3TmnW1hALm7SARrA            31.231   
1  3940805029337923  oahj3avp62i9333f14wq1b            27.290   
2   154327626587614  hxr4j9v5oazg96041bimr8            30.454   
3   476773713544002  4EDJVt3TmnW1hALm7SARrA            33.879   
4   803271957055341  4EDJVt3TmnW1hALm7SARrA            33.856   

   computed_altitude                                  camera_parameters  \
0           2.027818  [1.5235641673935, 0.087075630916789, 0.0063187...   
1           2.003059  [0.43952642366, 0.0607931433091, 0.00047321287...   
2           3.926726  [0.79644495704815, 0.11606791047681, 0.0402876...   
3           2.412898  [0.49681125152212, 0.14647653933878, 0.0689683...   
4           2.435879  [0.49681125152212, 0.14647653933878, 0.0689683...   

  camera_type               captured_at  compass_angle  \
0     fisheye 2019-10-23 14:53:03+00:00       36.03959   
1     fisheye 2019-10-22 11:43:09+00:00      215.11337   
2     fisheye 2019-10-23 14:23:07+00:00      321.71810   
3     fisheye 2019-10-23 14:50:24+00:00      141.03300   
4     fisheye 2019-10-23 14:50:23+00:00      142.48012   

   computed_compass_angle exif_orientation             merge_cc  \
0               36.750816                3  2730694295095799808   
1              215.920180                3  2730694295095799808   
2              324.158800                3  1699003678672699904   
3              146.524610                3  1699003678672699904   
4              147.678100                3  1699003678672699904   

                                                mesh  \
0  {'id': '488440382603236', 'url': 'https://scon...   
1                                               None   
2  {'id': '849892375616988', 'url': 'https://scon...   
3  {'id': '2564358967203782', 'url': 'https://sco...   
4  {'id': '533828757624761', 'url': 'https://scon...   

                                         sfm_cluster  \
0  {'id': '528674084929883', 'url': 'https://scon...   
1                         {'id': '1167304573740719'}   
2  {'id': '484032509534216', 'url': 'https://scon...   
3  {'id': '233453788582178', 'url': 'https://scon...   
4  {'id': '233453788582178', 'url': 'https://scon...   

                                          detections  \
0  {'data': [{'id': '1318687751867177'}, {'id': '...   
1  {'data': [{'id': '3949982768420149'}, {'id': '...   
2  {'data': [{'id': '155103619843348'}, {'id': '1...   
3  {'data': [{'id': '478803163341057'}, {'id': '4...   
4              {'data': [{'id': '805369486845588'}]}   

                                           image_url  \
0  https://storage.cloud.google.com/sudb_images/i...   
1  https://storage.cloud.google.com/sudb_images/i...   
2  https://storage.cloud.google.com/sudb_images/i...   
3  https://storage.cloud.google.com/sudb_images/i...   
4  https://storage.cloud.google.com/sudb_images/i...   

                                   computed_geometry  \
0  0101000020E610000095490436C3A16140F466DADF502E...   
1  0101000020E6100000F266351B9BA16140A5A13B3EA82D...   
2  0101000020E6100000154997283DA1614086A3EA1E812E...   
3  0101000020E61000004B7D6F9355A16140CDE35240272E...   
4  0101000020E6100000FF4450E654A16140A77F6DE6292E...   

                     geometry  
0  POINT (141.05508 42.36184)  
1  POINT (141.05018 42.35670)  
2  POINT (141.03872 42.36332)  
3  POINT (141.04169 42.36057)  
4  POINT (141.04161 42.36065)

## Visualize Data

We will use the `Visualize` class and folium maps to visualize the data. Before we can get started, we must initialize the Visualize class:

In [6]:
vis = Visualize(data)

Now we can map the locations of each image. We will make use of the simple Visualizer popup generator function to add popups that have images and basic metadata when markers are clicked.

In [7]:
map = folium.Map(location=[42.35849, 141.01552], tiles="OpenStreetMap", zoom_start=18)

images = [[point.xy[1][0], point.xy[0][0]] for point in data.geometry]

for i, coordinates in enumerate(images):
    html = vis.popup_html(i)
    popup = folium.Popup(folium.Html(html, script=True), max_width=500)
    map.add_child(
        folium.Marker(
            location=coordinates,
            popup=popup,
            icon=folium.Icon(),
        )
    )
 
map

Note that the bounding box should be small if mapping all features. Otherwise the map will render poorly. As a rule of thumb, try to keep this number less than 5000 or so.